In [1]:
import os
import time
import boto3
import pandas as pd
import sqlalchemy as sa 
from sqlalchemy import  MetaData
from sqlalchemy.orm import sessionmaker
from sqlalchemy.engine.url import URL
from sqlalchemy.schema import MetaData
from sqlalchemy.engine.url import URL
from sqlalchemy.ext.declarative import declarative_base
from dotenv import load_dotenv
from base import OtuCount, FeatureCountExtendedView
from scipy.spatial.distance import pdist, squareform

In [2]:
# Cargar variables de entorno
load_dotenv()

True

In [3]:
# Configuración de la conexión a la base de datos
def get_engine():
    url = URL.create(
        drivername=os.getenv('DB_DRIVER'),
        host=os.getenv('DB_HOST'),
        port=os.getenv('DB_PORT'),
        database=os.getenv('DB_NAME'),
        username=os.getenv('DB_USER'),
        password=os.getenv('DB_PASSWORD')
    )
    engine =sa.create_engine(url)
    return engine


In [4]:
def client(client):
    return boto3.client(
    client,
    aws_access_key_id=os.getenv('AWS_ACCESS_KEY_ID'),
    aws_secret_access_key=os.getenv('AWS_SECRET_ACCESS_KEY'),
    region_name=os.getenv('S3_REGION')
    )

In [5]:
engine = get_engine()
# Creación de MetaData y Declarative Base
metadata = MetaData()
Base = declarative_base(metadata=metadata)
# Creación de la sesión
Session = sessionmaker(bind=get_engine())
session = Session()
s3 = client('s3')
# Configurar el cliente de Athena
athena_client = client('athena')

In [6]:
def get_otu_all():
    """Consulta a la tabla Taxonomy con un límite especificado."""
    query = session.query(OtuCount)
    df = pd.read_sql(query.statement, session.bind)
    return df

In [7]:
def get_feature_all():
    """Consulta a la tabla Taxonomy con un límite especificado."""
    query = session.query(FeatureCountExtendedView)
    df = pd.read_sql(query.statement, session.bind)
    return df

In [8]:
def get_feature_otu():
    """Consulta a la tabla Taxonomy con un límite especificado."""
    query = session.query(
        FeatureCountExtendedView.value, 
        FeatureCountExtendedView.otu, 
        FeatureCountExtendedView.sampleId
    ).filter(FeatureCountExtendedView.projectId == 'E335')
    df = pd.read_sql(query.statement, session.bind)
    return df

In [9]:
def create_athena_table(athena_client, formatted_columns, location):
    # Formatear los nombres de las columnas

    # Definir la consulta DDL para crear la tabla
    ddl_query = f"""
        CREATE EXTERNAL TABLE IF NOT EXISTS siwa_test.otuse349 (
            index string,
            {formatted_columns}
        )
        STORED AS PARQUET
        LOCATION {location}
        TBLPROPERTIES ('classification'='parquet');
    """

    # Configurar el bucket de S3 para los resultados de la consulta
    output_location = 's3://siwamicrobiome/athenatest/otucountresults/'

    # Ejecutar la consulta DDL
    response = athena_client.start_query_execution(
        QueryString=ddl_query,
        ResultConfiguration={
            'OutputLocation': output_location,
        }
    )

    # Obtener el ID de ejecución de la consulta
    query_execution_id = response['QueryExecutionId']

    print(f"La tabla se está creando. ID de ejecución de la consulta: {query_execution_id}")



In [10]:
def run_athena_query(athena_client, query, database, s3_output):
    """
    Ejecuta una consulta SQL en Athena y devuelve el resultado.

    :param athena_client: Cliente de Athena.
    :param query: Consulta SQL a ejecutar.
    :param database: Base de datos de Athena.
    :param s3_output: Ubicación de S3 para los resultados de la consulta.
    :return: Resultado de la consulta o None si la consulta falla.
    """

    # Configuración de la ejecución de la consulta
    query_execution = athena_client.start_query_execution(
        QueryString=query,
        QueryExecutionContext={'Database': database},
        ResultConfiguration={'OutputLocation': s3_output}
    )

    # Esperar a que la consulta se complete
    query_execution_id = query_execution['QueryExecutionId']

    while True:
        # Obtener el estado actual de la ejecución de la consulta
        query_status = athena_client.get_query_execution(
            QueryExecutionId=query_execution_id
        )['QueryExecution']['Status']['State']

        if query_status in ['SUCCEEDED', 'FAILED', 'CANCELLED']:
            break

        print(f"Estado de la consulta: {query_status}. Esperando...")
        time.sleep(5)  # Espera 5 segundos antes de volver a verificar el estado

    if query_status == 'FAILED' or query_status == 'CANCELLED':
        raise Exception(f'La consulta de Athena no se completó. Estado: {query_status}')

    # Utiliza un paginador para manejar los resultados de la consulta
    paginator = athena_client.get_paginator('get_query_results')
    page_iterator = paginator.paginate(QueryExecutionId=query_execution_id)

    # Recorre cada página (cada una con hasta 1000 registros) y procesa los resultados
    all_results = []
    for page in page_iterator:
        for row in page['ResultSet']['Rows']:
            # Procesa cada fila
            all_results.append(row)

    return all_results

In [11]:
import pandas as pd

def pivotear_datos(df):
    """
    Pivotea los datos de un DataFrame.

    Parámetros:
    df (DataFrame): DataFrame que contiene las columnas 'value', 'otu' y 'sampleId'.

    Devuelve:
    DataFrame: DataFrame pivoteado con 'otu' como índice y 'sampleId' como columnas.
    """

    # Crear una tabla pivote
    datos_pivoteados = (
        df.pivot_table(values='value', index='otu', columns='sampleId')
          .fillna(0)
          .rename_axis(index=None, columns=None)
    )

    # Restablecer el índice
    datos_pivoteados = datos_pivoteados.reset_index()

    return datos_pivoteados

In [12]:
def calcular_matriz_distancia(df):
    """
    Calcula la matriz de distancia de Bray-Curtis a partir de un DataFrame.

    Parámetros:
    df (DataFrame): DataFrame de Pandas con la primera columna siendo un índice no necesario
                    y la columna 'index' conteniendo identificadores únicos (OTUs).
                    Las otras columnas representan las muestras.

    Devuelve:
    DataFrame: Matriz de distancia de Bray-Curtis.
    """

    # Establecer la columna 'index' como el índice del DataFrame
    df = df.set_index('index')

    # Transponer el DataFrame para que las muestras sean las filas y los OTUs sean las columnas
    df_transpuesto = df.rename_axis(index=None, columns=None).transpose()
    df_transpuesto = df_transpuesto.apply(pd.to_numeric, errors='coerce').fillna(0)

    # Calcular la matriz de distancia usando la métrica de Bray-Curtis
    matriz_distancia = pdist(df_transpuesto, metric='braycurtis')

    # Convertir la matriz de distancia a una matriz cuadrada (formato 2D)
    matriz_distancia_cuadrada = squareform(matriz_distancia)

    # Convertir a DataFrame para una mejor visualización
    matriz_distancia_df = pd.DataFrame(matriz_distancia_cuadrada, 
                                       index=df_transpuesto.index, 
                                       columns=df_transpuesto.index)

    return matriz_distancia_df

In [13]:
def convertir_a_dataframe(resultados):
    """
    Convierte una lista de resultados en un DataFrame de Pandas.

    Parámetros:
    resultados (list): Lista de resultados, donde cada resultado es un diccionario con claves 'Data'.

    Devuelve:
    DataFrame: DataFrame de Pandas construido a partir de los resultados.
    """

    # Verificar si la primera fila contiene los nombres de las columnas
    if all('VarCharValue' in d for d in resultados[0]['Data']):
        column_names = [d['VarCharValue'] for d in resultados[0]['Data']]
    else:
        raise KeyError("La primera fila no contiene los nombres de las columnas")

    # Crear una lista de diccionarios para las filas de datos
    rows = []
    for row in resultados[1:]:
        # Verificar si cada fila tiene la clave 'VarCharValue'
        if all('VarCharValue' in d for d in row['Data']):
            row_data = [d['VarCharValue'] for d in row['Data']]
            row_dict = dict(zip(column_names, row_data))
            rows.append(row_dict)
        else:
            # Aquí puedes decidir cómo manejar filas que no tienen 'VarCharValue'
            print("Fila ignorada o incompleta detectada")

    # Crear el DataFrame
    df = pd.DataFrame(rows)
    return df

In [14]:
df_feature_otu = get_feature_otu()

In [15]:
df_feature_otu

value                               otu  sampleId
0       11.0  0036a4e11fe7a350076bd7cfb698d458  0070_06C
1       11.0  0036a4e11fe7a350076bd7cfb698d458  0070_06C
2       11.0  0036a4e11fe7a350076bd7cfb698d458  0070_06C
3       26.0  0036a4e11fe7a350076bd7cfb698d458  0071_06C
4       26.0  0036a4e11fe7a350076bd7cfb698d458  0071_06C
...      ...                               ...       ...
48973   15.0  ff772f18ec3760046ea9dd413fc88de7  0083_01C
48974   15.0  ff772f18ec3760046ea9dd413fc88de7  0083_01C
48975   15.0  ff772f18ec3760046ea9dd413fc88de7  0083_01C
48976   72.0  fff9fd9fdd5a143852810cc1efda341f  0072_05C
48977   72.0  fff9fd9fdd5a143852810cc1efda341f  0072_05C

[48978 rows x 3 columns]

In [16]:
df_feature_otu.dtypes


value       float64
otu          object
sampleId     object
dtype: object

In [17]:
# df_otu_con_project es tu DataFrame
parquet_buffer = df_feature_otu.to_parquet( engine='pyarrow', compression='snappy')

c:\Users\jmontoyas\AppData\Local\miniconda3\envs\athena-aws\Lib\site-packages\pyarrow\pandas_compat.py:373: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if _pandas_api.is_sparse(col):


In [18]:
# Pivotear los datos
otutable = pivotear_datos(df_feature_otu)

In [19]:
otutable

index  0070_01C  0070_01F  0070_01I  \
0     0034f9f05383385c8111cbcfbb92e490       0.0       0.0       0.0   
1     0036a4e11fe7a350076bd7cfb698d458       0.0       0.0       0.0   
2     003ec3769586bba2e2fcd44397f96010       0.0       0.0       0.0   
3     00a26b2be8bc19e5315b238405f92e27       0.0       0.0       0.0   
4     0100806596ceb2439115b4dd3d7a1125       0.0       0.0       0.0   
...                                ...       ...       ...       ...   
1374  ff06bdea2515dff049f327b497d8922e       0.0       0.0       0.0   
1375  ff3739dd5a3c35cf09f01a391ce07570       0.0       0.0       0.0   
1376  ff772f18ec3760046ea9dd413fc88de7       0.0       0.0       0.0   
1377  ffa726ca59b93f4066a71285d5855dbd       0.0       0.0       0.0   
1378  fff9fd9fdd5a143852810cc1efda341f       0.0       0.0       0.0   

      0070_02C  0070_02F  0070_02I  0070_03C  0070_03F  0070_03I  ...  \
0          0.0       0.0       0.0       0.0       0.0       0.0  ...   
1          0.0       0.0       0.0       0.0       0.0       0.0  ...   
2          0.0       0.0       0.0       0.0       0.0       0.0  ...   
3          0.0       0.0       0.0       0.0       0.0       0.0  ...   
4          0.0       0.0       0.0       0.0       0.0       0.0  ...   
...        ...       ...       ...       ...       ...       ...  ...   
1374       0.0       0.0       0.0       0.0       0.0       0.0  ...   
1375       0.0       0.0       0.0       0.0       0.0       0.0  ...   
1376       0.0       0.0       0.0       0.0       0.0       0.0  ...   
1377       0.0       0.0       0.0       0.0       0.0       0.0  ...   
1378       0.0       0.0       0.0       0.0       0.0       0.0  ...   

      0086_03I  0086_04C  0086_04F  0086_04I  0086_05C  0086_05F  0086_05I  \
0          0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1          0.0       0.0       0.0       0.0      12.0       0.0       0.0   
2          0.0       0.0       0.0       0.0       0.0       0.0       0.0   
3          0.0       0.0       0.0       0.0       0.0       0.0       0.0   
4          0.0       0.0       0.0       0.0       0.0       0.0       0.0   
...        ...       ...       ...       ...       ...       ...       ...   
1374       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1375       0.0      27.0     130.0     200.0      35.0      82.0     104.0   
1376       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1377       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1378       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

      0086_06C  0086_06F  0086_06I  
0         26.0       0.0       0.0  
1          5.0       0.0       0.0  
2          0.0       0.0       0.0  
3          0.0       0.0       0.0  
4          0.0       0.0       0.0  
...        ...       ...       ...  
1374       0.0       0.0       0.0  
1375      51.0      74.0     122.0  
1376       0.0       0.0       0.0  
1377       0.0       0.0       0.0  
1378       0.0       0.0       0.0  

[1379 rows x 249 columns]

In [20]:

formatted_columns = ", ".join([f"{col} double" for col in otutable.columns[1:]])
location = "'s3://siwamicrobiome/athenatest/otucount/'"
create_athena_table(athena_client, formatted_columns, location)

La tabla se está creando. ID de ejecución de la consulta: 34166e34-e5bc-4ac4-9d41-1b601da3f285


In [21]:
# Lista de columnas a excluir
exclude_columns = ["0171_02F", "0171_01F"," 0171_04F", "0171_05F", "0171_06F", "0171_07F", "0171_08F", "0171_09F"]
# Formatear las columnas, excluyendo las especificadas
formatted_columns = ", ".join([f'"{col}"' for col in otutable.columns[1:] if col not in exclude_columns])
formatted_columns = ", ".join([f'"{col}"' for col in otutable.columns[1:]])
query = f"""SELECT * FROM otuse349"""
database = 'siwa_test'
s3_output = 's3://siwamicrobiome/athenatest/apiQueryResults'

resultados = run_athena_query(athena_client,query, database, s3_output)
resultados

Estado de la consulta: QUEUED. Esperando...


[{'Data': [{'VarCharValue': 'index'},
   {'VarCharValue': '0171_01f'},
   {'VarCharValue': '0171_02f'},
   {'VarCharValue': '0171_03f'},
   {'VarCharValue': '0171_04f'},
   {'VarCharValue': '0171_05f'},
   {'VarCharValue': '0171_06f'},
   {'VarCharValue': '0171_07f'},
   {'VarCharValue': '0171_08f'},
   {'VarCharValue': '0171_09f'},
   {'VarCharValue': '0171_10f'},
   {'VarCharValue': '0172_01f'},
   {'VarCharValue': '0172_02f'},
   {'VarCharValue': '0172_03f'},
   {'VarCharValue': '0172_04f'},
   {'VarCharValue': '0172_05f'},
   {'VarCharValue': '0172_06f'},
   {'VarCharValue': '0172_07f'},
   {'VarCharValue': '0172_08f'},
   {'VarCharValue': '0172_09f'},
   {'VarCharValue': '0172_10f'},
   {'VarCharValue': '0173_01f'},
   {'VarCharValue': '0173_02f'},
   {'VarCharValue': '0173_03f'},
   {'VarCharValue': '0173_04f'},
   {'VarCharValue': '0173_05f'},
   {'VarCharValue': '0173_06f'},
   {'VarCharValue': '0173_07f'},
   {'VarCharValue': '0173_08f'},
   {'VarCharValue': '0173_09f'},
   {'

In [22]:
# Crear el DataFrame
df_otus_parquet = convertir_a_dataframe(resultados)

df_otus_parquet

index 0171_01f 0171_02f 0171_03f 0171_04f  \
0     000173d54ec03bb63103cedd9c23ee43      0.0      0.0      0.0      0.0   
1     00287ac0b861934632cdd2b5550bd1ce      0.0      0.0      0.0      0.0   
2     003274c68c788d53b78131fb97fdf241      5.0      0.0      0.0      0.0   
3     0038f7e712480fa0bcecdd4f8305ae05      0.0      0.0      0.0      0.0   
4     0040984928ef0ec99754a4836c4ce077      0.0      0.0      0.0      0.0   
...                                ...      ...      ...      ...      ...   
6222  ffc9267421ff586ae8b721372a50bac0      0.0      0.0      0.0      0.0   
6223  ffc9ee85cbd6e13ad879dd85b9a3a1e1      0.0      0.0      0.0      0.0   
6224  ffcb2623137f828e32d7493655d57ea2      0.0      0.0      0.0     34.0   
6225  ffd799eb4e6ba3736249983463c64f72      0.0      0.0      0.0      0.0   
6226  fff74caa18f09f4cabe7e1a1314bf091      0.0     31.0     74.0     32.0   

     0171_05f 0171_06f 0171_07f 0171_08f 0171_09f  ... 0194_01f 0194_02f  \
0         0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
1         0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2         0.0      0.0      0.0     60.0      0.0  ...      0.0      0.0   
3         0.0     33.0      0.0      0.0      0.0  ...      0.0      0.0   
4         0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
...       ...      ...      ...      ...      ...  ...      ...      ...   
6222      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
6223      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
6224      0.0      0.0      0.0      6.0      0.0  ...      0.0      0.0   
6225      0.0      0.0      0.0      0.0      0.0  ...      5.0      0.0   
6226      0.0      8.0      0.0      0.0     15.0  ...      4.0      0.0   

     0194_03f 0194_04f 0194_05f 0194_06f 0194_07f 0194_08f 0194_09f 0194_10f  
0         0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1         0.0      0.0      7.0      0.0      0.0      0.0      0.0      0.0  
2         0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3         0.0      0.0      0.0      0.0      0.0      5.0      0.0      0.0  
4         0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
...       ...      ...      ...      ...      ...      ...      ...      ...  
6222      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
6223      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
6224      0.0      0.0      0.0      0.0      0.0      0.0    107.0      0.0  
6225      0.0      0.0      0.0      5.0      0.0      0.0      0.0     11.0  
6226      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[6227 rows x 241 columns]

In [23]:
df_otus_parquet

index 0171_01f 0171_02f 0171_03f 0171_04f  \
0     000173d54ec03bb63103cedd9c23ee43      0.0      0.0      0.0      0.0   
1     00287ac0b861934632cdd2b5550bd1ce      0.0      0.0      0.0      0.0   
2     003274c68c788d53b78131fb97fdf241      5.0      0.0      0.0      0.0   
3     0038f7e712480fa0bcecdd4f8305ae05      0.0      0.0      0.0      0.0   
4     0040984928ef0ec99754a4836c4ce077      0.0      0.0      0.0      0.0   
...                                ...      ...      ...      ...      ...   
6222  ffc9267421ff586ae8b721372a50bac0      0.0      0.0      0.0      0.0   
6223  ffc9ee85cbd6e13ad879dd85b9a3a1e1      0.0      0.0      0.0      0.0   
6224  ffcb2623137f828e32d7493655d57ea2      0.0      0.0      0.0     34.0   
6225  ffd799eb4e6ba3736249983463c64f72      0.0      0.0      0.0      0.0   
6226  fff74caa18f09f4cabe7e1a1314bf091      0.0     31.0     74.0     32.0   

     0171_05f 0171_06f 0171_07f 0171_08f 0171_09f  ... 0194_01f 0194_02f  \
0         0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
1         0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2         0.0      0.0      0.0     60.0      0.0  ...      0.0      0.0   
3         0.0     33.0      0.0      0.0      0.0  ...      0.0      0.0   
4         0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
...       ...      ...      ...      ...      ...  ...      ...      ...   
6222      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
6223      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
6224      0.0      0.0      0.0      6.0      0.0  ...      0.0      0.0   
6225      0.0      0.0      0.0      0.0      0.0  ...      5.0      0.0   
6226      0.0      8.0      0.0      0.0     15.0  ...      4.0      0.0   

     0194_03f 0194_04f 0194_05f 0194_06f 0194_07f 0194_08f 0194_09f 0194_10f  
0         0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1         0.0      0.0      7.0      0.0      0.0      0.0      0.0      0.0  
2         0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3         0.0      0.0      0.0      0.0      0.0      5.0      0.0      0.0  
4         0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
...       ...      ...      ...      ...      ...      ...      ...      ...  
6222      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
6223      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
6224      0.0      0.0      0.0      0.0      0.0      0.0    107.0      0.0  
6225      0.0      0.0      0.0      5.0      0.0      0.0      0.0     11.0  
6226      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[6227 rows x 241 columns]

In [24]:
matriz_distancia = calcular_matriz_distancia(df_otus_parquet)

In [25]:
matriz_distancia

0171_01f  0171_02f  0171_03f  0171_04f  0171_05f  0171_06f  \
0171_01f  0.000000  0.469200  0.520719  0.650246  0.582201  0.669654   
0171_02f  0.469200  0.000000  0.408863  0.624885  0.574893  0.778191   
0171_03f  0.520719  0.408863  0.000000  0.592189  0.637109  0.779943   
0171_04f  0.650246  0.624885  0.592189  0.000000  0.807889  0.731617   
0171_05f  0.582201  0.574893  0.637109  0.807889  0.000000  0.860650   
...            ...       ...       ...       ...       ...       ...   
0194_06f  0.861714  0.777118  0.709219  0.588641  0.933668  0.796300   
0194_07f  0.752365  0.693703  0.686182  0.524994  0.848413  0.778474   
0194_08f  0.745630  0.692699  0.618346  0.477040  0.872186  0.783946   
0194_09f  0.921717  0.880770  0.847362  0.833361  0.939753  0.939074   
0194_10f  0.832486  0.780626  0.771614  0.710868  0.922004  0.731263   

          0171_07f  0171_08f  0171_09f  0171_10f  ...  0194_01f  0194_02f  \
0171_01f  0.513956  0.520894  0.545544  0.501070  ...  0.720108  0.820705   
0171_02f  0.425347  0.417237  0.549163  0.423407  ...  0.677820  0.694480   
0171_03f  0.466610  0.426034  0.488541  0.396291  ...  0.642891  0.628928   
0171_04f  0.702134  0.416492  0.482203  0.556815  ...  0.597186  0.566555   
0171_05f  0.496012  0.655275  0.719792  0.668017  ...  0.793603  0.854339   
...            ...       ...       ...       ...  ...       ...       ...   
0194_06f  0.824616  0.652220  0.658869  0.737394  ...  0.601426  0.385686   
0194_07f  0.724966  0.541704  0.586302  0.668520  ...  0.526309  0.431996   
0194_08f  0.724878  0.542626  0.551307  0.619667  ...  0.602915  0.353301   
0194_09f  0.891153  0.855783  0.821296  0.863921  ...  0.790176  0.783391   
0194_10f  0.793413  0.732917  0.624627  0.699707  ...  0.540043  0.668074   

          0194_03f  0194_04f  0194_05f  0194_06f  0194_07f  0194_08f  \
0171_01f  0.792322  0.756676  0.795253  0.861714  0.752365  0.745630   
0171_02f  0.690678  0.641690  0.717817  0.777118  0.693703  0.692699   
0171_03f  0.625110  0.608079  0.666491  0.709219  0.686182  0.618346   
0171_04f  0.558552  0.520492  0.521944  0.588641  0.524994  0.477040   
0171_05f  0.871947  0.829471  0.884753  0.933668  0.848413  0.872186   
...            ...       ...       ...       ...       ...       ...   
0194_06f  0.409415  0.382462  0.331131  0.000000  0.384487  0.355749   
0194_07f  0.365446  0.399950  0.275081  0.384487  0.000000  0.363542   
0194_08f  0.373316  0.314829  0.319932  0.355749  0.363542  0.000000   
0194_09f  0.801114  0.811425  0.810447  0.805693  0.801554  0.783355   
0194_10f  0.627044  0.617634  0.614137  0.579668  0.618876  0.638428   

          0194_09f  0194_10f  
0171_01f  0.921717  0.832486  
0171_02f  0.880770  0.780626  
0171_03f  0.847362  0.771614  
0171_04f  0.833361  0.710868  
0171_05f  0.939753  0.922004  
...            ...       ...  
0194_06f  0.805693  0.579668  
0194_07f  0.801554  0.618876  
0194_08f  0.783355  0.638428  
0194_09f  0.000000  0.826573  
0194_10f  0.826573  0.000000  

[240 rows x 240 columns]